# Experiments master thesis ETH

### Install packages

In [1]:
!pip3 install backpack-for-pytorch
!pip3 install asdfghjkl
!pip3 install laplace-torch
!pip3 install laplace
!python3 -m pip install laplace-torch
!pip3 install tqdm

  Using cached backpack_for_pytorch-1.5.2-py3-none-any.whl (183 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 887.5/887.5 MB 603.3 kB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.0/6.0 MB 25.5 MB/s eta 0:00:00:00:0100:01
  Using cached einops-0.6.1-py3-none-any.whl (42 kB)
  Using cached nvidia_cublas_cu11-11.10.3.66-py3-none-manylinux1_x86_64.whl (317.1 MB)
  Using cached nvidia_cuda_nvrtc_cu11-11.7.99-2-py3-none-manylinux1_x86_64.whl (21.0 MB)
  Using cached nvidia_cudnn_cu11-8.5.0.96-2-py3-none-manylinux1_x86_64.whl (557.1 MB)
  Using cached nvidia_cuda_runtime_cu11-11.7.99-py3-none-manylinux1_x86_64.whl (849 kB)
  Using cached typing_extensions-4.5.0-py3-none-any.whl (27 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.5/64.5 KB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.2/24.2 MB 26.3 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 44.6 MB/s eta 0:00:00:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━

In [2]:
import sys
sys.path
sys.path.append('/home/infres/slabbi/Master_thesis/lib/python3.8/site-packages')

In [3]:
torch.cuda.is_available()
torch.cuda.device_count()
torch.cuda.current_device()
torch.cuda.device(0)
torch.cuda.get_device_name(0)

'Tesla V100-PCIE-16GB'

In [2]:
import torch
X_train = torch.FloatTensor([0., 1., 2.]).cuda()
X_train.is_cuda

True

In [4]:
!nvidia-smi

Sun Apr 30 22:30:52 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 515.65.01    Driver Version: 515.65.01    CUDA Version: 11.7     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-PCIE...  Off  | 00000000:3B:00.0 Off |                    0 |
| N/A   28C    P0    36W / 250W |   1416MiB / 16384MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  Tesla V100-PCIE...  Off  | 00000000:AF:00.0 Off |                    0 |
| N/A   

## Marginal likehood optimisation

In [5]:
from copy import deepcopy
import numpy as np
import torch
from torch.nn.utils.convert_parameters import vector_to_parameters
from torch.optim import Adam, SGD
from torch.optim.lr_scheduler import ExponentialLR, CosineAnnealingLR
from torch.nn import CrossEntropyLoss, MSELoss
from torch.nn.utils import parameters_to_vector
from torch.distributions import Normal
import matplotlib.pyplot as plt
import math
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.distributions as td
from torchvision import datasets, transforms
from torchvision.utils import make_grid
from tqdm import tqdm, trange

from laplace.baselaplace import KronLaplace
from laplace.curvature import AsdlGGN


GB_FACTOR = 1024 ** 3




def expand_prior_precision(prior_prec, model):
    theta = parameters_to_vector(model.parameters())
    device, P = theta.device, len(theta)
    assert prior_prec.ndim == 1
    if len(prior_prec) == 1:  # scalar
        return torch.ones(P, device=device) * prior_prec
    elif len(prior_prec) == P:  # full diagonal
        return prior_prec.to(device)
    else:
        return torch.cat([delta * torch.ones_like(m).flatten() for delta, m
                          in zip(prior_prec, model.parameters())])




def get_prior_hyperparams(prior_prec_init, prior_structure, H, P, device):
    log_prior_prec_init = np.log(prior_prec_init)
    if prior_structure == 'scalar':
        log_prior_prec = log_prior_prec_init * torch.ones(1, device=device)
    elif prior_structure == 'layerwise':
        log_prior_prec = log_prior_prec_init * torch.ones(H, device=device)
    elif prior_structure == 'diagonal':
        log_prior_prec = log_prior_prec_init * torch.ones(P, device=device)
    else:
        raise ValueError(f'Invalid prior structure {prior_structure}')
    log_prior_prec.requires_grad = True
    return log_prior_prec




def valid_performance(model, test_loader, likelihood, criterion, device):
    N = len(test_loader.dataset)
    perf = 0
    nll = 0
    for X, y in test_loader:
        X, y = X.detach().to(device), y.detach().to(device)
        with torch.no_grad():
            f = model(X)
        if likelihood == 'classification':
            perf += (torch.argmax(f, dim=-1) == y).sum() / N
        elif likelihood == 'heteroscedastic_regression':
            perf += (y.squeeze() + 0.5 * f[:, 0] / f[:, 1]).square().sum() / N
        else:
            perf += (f - y).square().sum() / N
        nll += criterion(f, y) / len(test_loader)
    return perf.item(), nll.item()




def get_scheduler(scheduler, optimizer, train_loader, n_epochs, lr, lr_min):
    n_steps = n_epochs * len(train_loader)
    if scheduler == 'exp':
        min_lr_factor = lr_min / lr
        gamma = np.exp(np.log(min_lr_factor) / n_steps)
        return ExponentialLR(optimizer, gamma=gamma)
    elif scheduler == 'cos':
        return CosineAnnealingLR(optimizer, n_steps, eta_min=lr_min)
    else:
        raise ValueError(f'Invalid scheduler {scheduler}')




def get_model_optimizer(optimizer, model, lr, weight_decay=0):
    if optimizer == 'adam':
        return Adam(model.parameters(), lr=lr, weight_decay=weight_decay)
    elif optimizer == 'sgd':
        # fixup parameters should have 10x smaller learning rate
        is_fixup = lambda param: param.size() == torch.Size([1])  # scalars
        fixup_params = [p for p in model.parameters() if is_fixup(p)]
        standard_params = [p for p in model.parameters() if not is_fixup(p)]
        params = [{'params': standard_params}, {'params': fixup_params, 'lr': lr / 10.}]
        return SGD(params, lr=lr, momentum=0.9, weight_decay=weight_decay)
    else:
        raise ValueError(f'Invalid optimizer {optimizer}')




def gradient_to_vector(parameters):
    return parameters_to_vector([e.grad for e in parameters])




def vector_to_gradient(vec, parameters):
    return vector_to_parameters(vec, [e.grad for e in parameters])




def marglik_optimization(model,
                         train_loader,
                         valid_loader=None,
                         likelihood='classification',
                         prior_structure='layerwise',
                         prior_prec_init=1.,
                         sigma_noise_init=1.,
                         temperature=1.,
                         n_epochs=50,
                         lr=1e-3,
                         lr_min=None,
                         optimizer='Adam',
                         scheduler='cos',
                         n_epochs_burnin=0,
                         n_hypersteps=100,
                         marglik_frequency=1,
                         lr_hyp=1e-1,
                         lr_hyp_min=1e-1,
                         laplace=KronLaplace,
                         backend=AsdlGGN,
                         early_stopping=False):
    """Runs marglik optimization training for a given model and training dataloader.


    Parameters
    ----------
    model : torch.nn.Module
        torch model
    train_loader : DataLoader
        pytorch training dataset loader
    valid_loader : DataLoader
    likelihood : str
        'classification', 'regression', 'heteroscedastic_regression'
    prior_structure : str
        'scalar', 'layerwise', 'diagonal'
    prior_prec_init : float
        initial prior precision
    sigma_noise_init : float
        initial observation noise (for regression only)
    temperature : float
        factor for the likelihood for 'overcounting' data.
        Often required when using data augmentation.
    n_epochs : int
    lr : float
        learning rate for model optimizer
    lr_min : float
        minimum learning rate, defaults to lr and hence no decay
        to have the learning rate decay from 1e-3 to 1e-6, set
        lr=1e-3 and lr_min=1e-6.
    optimizer : str
        either 'adam' or 'sgd'
    scheduler : str
        either 'exp' for exponential and 'cos' for cosine decay towards lr_min
    n_epochs_burnin : int default=0
        how many epochs to train without estimating and differentiating marglik
    n_hypersteps : int
        how many steps to take on the hyperparameters when marglik is estimated
    marglik_frequency : int
        how often to estimate (and differentiate) the marginal likelihood
    lr_hyp : float
        learning rate for hyperparameters (should be between 1e-3 and 1)
    laplace : Laplace
        type of Laplace approximation (Kron/Diag/Full)
    backend : Backend
        AsdlGGN/AsdlEF or BackPackGGN/BackPackEF
    stochastic_grad : bool
    independent : bool
        whether to use independent functional laplace
    single_output : bool
        whether to use single random output for functional laplace
    kron_jac : bool
        whether to use kron_jac in the backend


    Returns
    -------
    lap : Laplace
        lapalce approximation
    model : torch.nn.Module
    margliks : list
    losses : list
    """
    if lr_min is None:  # don't decay lr
        lr_min = lr
    device = parameters_to_vector(model.parameters()).device
    N = len(train_loader.dataset)
    H = len(list(model.parameters()))
    P = len(parameters_to_vector(model.parameters()))
    best_model_dict = None


    # differentiable hyperparameters
    hyperparameters = list()
    # prior precision
    log_prior_prec = get_prior_hyperparams(prior_prec_init, prior_structure, H, P, device)
    hyperparameters.append(log_prior_prec)


    # set up loss (and observation noise hyperparam)
    if likelihood == 'classification':
        criterion = CrossEntropyLoss(reduction='mean')
        sigma_noise = 1
    elif likelihood == 'regression':
        criterion = MSELoss(reduction='mean')
        log_sigma_noise_init = np.log(sigma_noise_init)
        log_sigma_noise = log_sigma_noise_init * torch.ones(1, device=device)
        log_sigma_noise.requires_grad = True
        hyperparameters.append(log_sigma_noise)
    else:
        raise ValueError()


    # set up model optimizer and scheduler
    optimizer = get_model_optimizer(optimizer, model, lr)
    scheduler = get_scheduler(scheduler, optimizer, train_loader, n_epochs, lr, lr_min)


    n_steps = ((n_epochs - n_epochs_burnin) // marglik_frequency) * n_hypersteps
    hyper_optimizer = Adam(hyperparameters, lr=lr_hyp)
    hyper_scheduler = CosineAnnealingLR(hyper_optimizer, n_steps, eta_min=lr_hyp_min)


    losses = list()
    valid_perfs = list()
    valid_nlls = list()
    margliks = list()
    best_marglik = np.inf


    for epoch in range(1, n_epochs + 1):
        epoch_loss = 0
        epoch_perf = 0
        epoch_nll = 0
        epoch_log = dict(epoch=epoch)


        # standard NN training per batch
        torch.cuda.empty_cache()
        for X, y in train_loader:
            X, y = X.detach().to(device), y.to(device)
            optimizer.zero_grad()


            if likelihood == 'regression':
                sigma_noise = torch.exp(log_sigma_noise).detach()
                crit_factor = 1 / temperature / (2 * sigma_noise.square())
            else:
                crit_factor = 1 / temperature
            prior_prec = torch.exp(log_prior_prec).detach()
            delta = expand_prior_precision(prior_prec, model)


            f = model(X)


            theta = parameters_to_vector(model.parameters())
            loss = criterion(f, y) + (0.5 * (delta * theta) @ theta) / N / crit_factor
            loss.backward()
            optimizer.step()


            epoch_loss += loss.cpu().item() / len(train_loader)
            epoch_nll += criterion(f.detach(), y).item() / len(train_loader)
            if likelihood == 'regression':
                epoch_perf += (f.detach() - y).square().sum() / N
            elif likelihood == 'heteroscedastic_regression':
                epoch_perf += (y.squeeze() + 0.5 * f[:, 0] / f[:, 1]).square().sum() / N
            else:
                epoch_perf += torch.sum(torch.argmax(f.detach(), dim=-1) == y).item() / N
            scheduler.step()


        losses.append(epoch_loss)
        logging.info(f'MARGLIK[epoch={epoch}]: train. perf={epoch_perf:.2f}; loss={epoch_loss:.5f}; nll={epoch_nll:.5f}')
        optimizer.zero_grad(set_to_none=True)
        llr = scheduler.get_last_lr()[0]
        epoch_log.update({'train/loss': epoch_loss, 'train/nll': epoch_nll, 'train/perf': epoch_perf, 'train/lr': llr})
        # compute validation error to report during training
        if valid_loader is not None:
            with torch.no_grad():
                if likelihood == 'regression':
                    def val_criterion(f, y):
                        assert f.shape == y.shape
                        log_lik = Normal(loc=f, scale=sigma_noise).log_prob(y)
                        return -log_lik.mean()
                else:
                    val_criterion = criterion
                val_perf, val_nll = valid_performance(model, valid_loader, likelihood, val_criterion, device)
                valid_perfs.append(val_perf)
                valid_nlls.append(val_nll)
                logging.info(f'MARGLIK[epoch={epoch}]: valid. perf={val_perf:.2f}; nll={val_nll:.5f}.')
                epoch_log.update({'valid/perf': val_perf, 'valid/nll': val_nll})


        # only update hyperparameters every "Frequency" steps after "burnin"
        if (epoch % marglik_frequency) != 0 or epoch < n_epochs_burnin:
            continue


        # 1. fit laplace approximation
        torch.cuda.empty_cache()


        sigma_noise = 1 if likelihood != 'regression' else torch.exp(log_sigma_noise)
        prior_prec = torch.exp(log_prior_prec)
        lap = laplace(model, likelihood, sigma_noise=sigma_noise, prior_precision=prior_prec,
                        temperature=temperature, backend=backend)
        lap.fit(train_loader)
        # first optimize prior precision jointly with direct marglik grad
        margliks_local = list()
        for i in range(n_hypersteps):
            hyper_optimizer.zero_grad()
            sigma_noise = None if likelihood != 'regression' else torch.exp(log_sigma_noise)
            prior_prec = torch.exp(log_prior_prec)
            marglik = -lap.log_marginal_likelihood(prior_prec, sigma_noise) / N
            marglik.backward()
            margliks_local.append(marglik.item())
            hyper_optimizer.step()
            hyper_scheduler.step()


        marglik = margliks_local[-1]


        if likelihood == 'regression':
            epoch_log['hyperparams/sigma_noise'] = torch.exp(log_sigma_noise.detach()).cpu().item()
        epoch_log['train/marglik'] = marglik
        margliks.append(marglik)
        del lap


        # early stopping on marginal likelihood
        if early_stopping and (margliks[-1] < best_marglik):
            best_model_dict = deepcopy(model.state_dict())
            best_precision = deepcopy(prior_prec.detach())
            best_sigma = 1 if likelihood != 'regression' else deepcopy(sigma_noise.detach())
            best_marglik = margliks[-1]


    if early_stopping and (best_model_dict is not None):
        model.load_state_dict(best_model_dict)
        sigma_noise = best_sigma
        prior_prec = best_precision
    else:
        sigma_noise = 1 if sigma_noise is None else sigma_noise


    lap = laplace(model, likelihood, sigma_noise=sigma_noise, prior_precision=prior_prec,
                  temperature=temperature, backend=backend)
    lap.fit(train_loader)
    return lap, model, margliks

In [6]:
import torch
import logging
import torch.nn as nn
from PBB.pbb.models import ProbNNet4l, NNet4l, CNNet4l
import torchvision
import math

class NNetmll(nn.Module):
    """Implementation of a standard Neural Network with 4 layers and dropout
    (used for the experiments on MNIST so it assumes a specific input size and
    number of classes)

    Parameters
    ----------
    dropout_prob : float
        probability of an element to be zeroed.

    device : string
        Device the code will run in (e.g. 'cuda')

    """

    def __init__(self, device='cuda'):
        super().__init__()
        self.l1 = nn.Linear(28*28, 600, device)
        self.l2 = nn.Linear(600, 600, device)
        self.l3 = nn.Linear(600, 600, device)
        self.l4 = nn.Linear(600, 10, device)

    def forward(self, x):
        # forward pass for the network
        x = x.view(-1, 28*28)
        x = self.l1(x)
        x = F.relu(x)
        x = self.l2(x)
        x = F.relu(x)
        x = self.l3(x)
        x = F.relu(x)
        return x
    
class CNNetmlll(nn.Module):
    """Implementation of a standard Convolutional Neural Network with 4 layers
    (used for the experiments on MNIST so it assumes a specific input size and
    number of classes)

    Parameters
    ----------
    dropout_prob : float
        probability of an element to be zeroed.

    device : string
        Device the code will run in (e.g. 'cuda')

    """

    def __init__(self, device='cuda'):
        super().__init__()
        self.conv1 = nn.Conv2d(1, 32, 3, 1)
        self.conv2 = nn.Conv2d(32, 64, 3, 1)
        self.fc1 = nn.Linear(9216, 128)
        self.fc2 = nn.Linear(128, 10)

    def forward(self, x):
        x = self.conv1(x)
        x = F.relu(x)
        x = self.conv2(x)
        x = F.relu(x)
        x = F.max_pool2d(x, 2)
        x = torch.flatten(x, 1)
        x = self.fc1(x)
        x = F.relu(x)
        x = self.fc2(x)
        return x
    
    
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(torch.cuda.is_available())

BATCH_SIZE = 250
TRAIN_EPOCHS = 1
DELTA = 0.025
DELTA_TEST = 0.01
PRIOR = 'rand'
dropout_prob = 0.0
SIGMAPRIOR = 0.03
rho_prior = math.log(math.exp(SIGMAPRIOR)-1.0)
PMIN = 1e-5
KL_PENALTY = 0.1
LEARNING_RATE = 0.001
MOMENTUM = 0.95
LEARNING_RATE_PRIOR = 0.005
MOMENTUM_PRIOR = 0.99

net0 = NNetmll(device=device).to(device)

net = CNNetmlll(device=device).to(device)

transform = torchvision.transforms.Compose([torchvision.transforms.ToTensor()])

train_dataset = torchvision.datasets.MNIST(
    root="~/torch_datasets", train=True, transform=transform, download=True
)

test_dataset = torchvision.datasets.MNIST(
    root="~/torch_datasets", train=False, transform=transform, download=True
)

train_loader = torch.utils.data.DataLoader(
    train_dataset, batch_size=128, shuffle=True, num_workers=4, pin_memory=True
)

test_loader = torch.utils.data.DataLoader(
    test_dataset, batch_size=32, shuffle=False, num_workers=4
)

lap, model, margliks = marglik_optimization(net,
                                             train_loader,
                                             valid_loader=test_loader,
                                             likelihood='classification',
                                             prior_structure='layerwise',
                                             prior_prec_init=1.,
                                             sigma_noise_init=1.,
                                             temperature=1.,
                                             n_epochs=1,
                                             lr=1e-3,
                                             lr_min=None,
                                             optimizer='adam',
                                             scheduler='cos',
                                             n_epochs_burnin=0,
                                             n_hypersteps=1,
                                             marglik_frequency=1,
                                             lr_hyp=1e-1,
                                             lr_hyp_min=1e-1,
                                             laplace=KronLaplace,
                                             backend=AsdlGGN,
                                             early_stopping=False)

True


In [7]:
net.eval()
with torch.no_grad():
    counter = 0
    total = 0
    for batch_id, (data, target) in enumerate(tqdm(test_loader)):
            data, target = data.to(device), target.to(device)
            prediction =  torch.argmax(model(data),axis =1)
            correct = torch.sum(target == prediction)
            counter += correct.item()
            shape= target.size()
            total += shape[0]
    print("The accuracy is equal to", counter/total)

100%|████████████████████████████████████████████████████████████████████████████████| 313/313 [00:00<00:00, 416.78it/s]

The accuracy is equal to 0.9826


## PAC-Bayes with Backprop

## Parameters

In [8]:
import torch
from PBB.pbb.utils import runexp
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(torch.cuda.is_available())

BATCH_SIZE = 250
TRAIN_EPOCHS = 50
DELTA = 0.025
DELTA_TEST = 0.01
PRIOR = 'learnt'

SIGMAPRIOR = 0.03

PMIN = 1e-5
KL_PENALTY = 0.1
LEARNING_RATE = 0.001
MOMENTUM = 0.95
LEARNING_RATE_PRIOR = 0.005
MOMENTUM_PRIOR = 0.99

# note the number of MC samples used in the paper is 150.000, which usually takes a several hours to compute
MC_SAMPLES = 1000


True


## CNN and flambda loss

In [13]:
runexp('mnist', 'flamb', PRIOR, 'cnn', SIGMAPRIOR, PMIN, LEARNING_RATE, MOMENTUM, LEARNING_RATE_PRIOR, MOMENTUM_PRIOR, delta=DELTA, delta_test=DELTA_TEST, mc_samples=MC_SAMPLES, train_epochs=TRAIN_EPOCHS, device=DEVICE, prior_epochs=70, perc_train=1.0, perc_prior=0.5, verbose=True, dropout_prob=0.2)

  1%|█▏                                                                                  | 1/70 [00:04<05:25,  4.71s/it]

-Epoch 0.00000, Train loss: 0.89773, Train err:  0.26157



  3%|██▍                                                                                 | 2/70 [00:09<05:25,  4.79s/it]

-Epoch 1.00000, Train loss: 0.23500, Train err:  0.06813



  4%|███▌                                                                                | 3/70 [00:14<05:17,  4.74s/it]

...


 54%|███████████████████████████████████████████▌                                     | 129/240 [00:09<00:07, 14.32it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 50/50 [14:45<00:00, 17.70s/it]


-Batch average epoch 49 results, Train obj: 0.00636, KL/n: 0.00022, NLL loss: 0.00280, Train 0-1 Error:  0.00624
-After optimising lambda: Train obj: 0.00648, KL/n: 0.00022, NLL loss: 0.00286, Train 0-1 Error:  0.00634, last lambda value: 0.99753


100%|███████████████████████████████████████████████████████████████████████████████████| 40/40 [00:34<00:00,  1.15it/s]

***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
flamb, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.03469, 0.02092, 0.03235, 0.00022, 0.01701, 0.02748, 0.00544, 0.01150, 0.00514, 0.01030, 0.00023, 0.00990, 0.01060, 1.00000, 0.50000


***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
flamb, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.03469, 0.02092, 0.03235, 0.00022, 0.01701, 0.02748, 0.00544, 0.01150, 0.00514, 0.01030, 0.00023, 0.00990, 0.01060, 1.00000, 0.50000

## CNN and fbbb loss

In [5]:
# note all of these running examples have different settings!

runexp('mnist', 'bbb', PRIOR, 'cnn', SIGMAPRIOR, PMIN, LEARNING_RATE, MOMENTUM, LEARNING_RATE_PRIOR, MOMENTUM_PRIOR, delta=DELTA, delta_test=DELTA_TEST, mc_samples=MC_SAMPLES, train_epochs=TRAIN_EPOCHS, device=DEVICE, perc_train=1.0, verbose=True, dropout_prob=0.2)


  0%|                                                                                                                                | 0/48 [00:00<?, ?it/s]/home/infres/slabbi/Master_thesis/lib/python3.10/site-packages/torch/nn/functional.py:1331: UserWarning: dropout2d: Received a 2-D input to dropout2d, which is deprecated and will result in an error in a future release. To retain the behavior and silence this warning, please use dropout instead. Note that dropout2d exists to provide channel-wise dropout on inputs with 2 spatial dimensions, a channel dimension, and an optional batch dimension (i.e. 3D or 4D inputs).
  warnings.warn(warn_msg)

  5%|██████                                                                                                                  | 1/20 [00:04<01:34,  4.99s/it]

-Epoch 0.00000, Train loss: 1.49087, Train err:  0.41525



 10%|████████████                                                                                                            | 2/20 [00:07<01:02,  3.46s/it]

-Epoch 1.00000, Train loss: 0.61055, Train err:  0.17367



 15%|██████████████████                                                                                                      | 3/20 [00:09<00:50,  2.99s/it]

...


 84%|█████████████████████████████████████████████████████████████████████████████████████████████████▉                   | 201/240 [00:16<00:03, 11.37it/s]


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [16:35<00:00, 19.92s/it]


-Batch average epoch 49 results, Train obj: 0.04716, KL/n: 0.00966, NLL loss: 0.03751, Train 0-1 Error:  0.01081


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 40/40 [00:34<00:00,  1.17it/s]

***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
bbb, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.02409, 0.03793, 0.05945, 0.00963, 0.01446, 0.02942, 0.00423, 0.01390, 0.00418, 0.01200, 0.00008, 0.01180, 0.01660, 1.00000, 0.20000


***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
bbb, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.02409, 0.03793, 0.05945, 0.00963, 0.01446, 0.02942, 0.00423, 0.01390, 0.00418, 0.01200, 0.00008, 0.01180, 0.01660, 1.00000, 0.20000

## CNN and fquad loss

In [9]:
runexp('mnist', 'fquad', PRIOR, 'cnn', SIGMAPRIOR, PMIN, LEARNING_RATE, MOMENTUM, LEARNING_RATE_PRIOR, MOMENTUM_PRIOR, delta=DELTA, delta_test=DELTA_TEST, mc_samples=MC_SAMPLES, train_epochs=TRAIN_EPOCHS, device=DEVICE, perc_train=1.0, verbose=True, dropout_prob=0.2)


  0%|                                                                                            | 0/48 [00:00<?, ?it/s]/home/infres/slabbi/Master_thesis/lib/python3.10/site-packages/torch/nn/functional.py:1331: UserWarning: dropout2d: Received a 2-D input to dropout2d, which is deprecated and will result in an error in a future release. To retain the behavior and silence this warning, please use dropout instead. Note that dropout2d exists to provide channel-wise dropout on inputs with 2 spatial dimensions, a channel dimension, and an optional batch dimension (i.e. 3D or 4D inputs).
  warnings.warn(warn_msg)

  5%|████▏                                                                               | 1/20 [00:01<00:35,  1.86s/it]

-Epoch 0.00000, Train loss: 1.49087, Train err:  0.41525



 10%|████████▍                                                                           | 2/20 [00:03<00:34,  1.90s/it]

-Epoch 1.00000, Train loss: 0.61055, Train err:  0.17367



 15%|████████████▌                                                                       | 3/20 [00:05<00:32,  1.89s/it]

...


 54%|███████████████████████████████████████████▌                                     | 129/240 [00:07<00:06, 18.22it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 50/50 [11:57<00:00, 14.35s/it]


-Batch average epoch 49 results, Train obj: 0.00767, KL/n: 0.00005, NLL loss: 0.00590, Train 0-1 Error:  0.01575


100%|███████████████████████████████████████████████████████████████████████████████████| 40/40 [00:35<00:00,  1.14it/s]

***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
fquad, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.02327, 0.02326, 0.04173, 0.00006, 0.02006, 0.03746, 0.00645, 0.01800, 0.00640, 0.01580, 0.00013, 0.01620, 0.01660, 1.00000, 0.20000


***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
fquad, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.02327, 0.02326, 0.04173, 0.00006, 0.02006, 0.03746, 0.00645, 0.01800, 0.00640, 0.01580, 0.00013, 0.01620, 0.01660, 1.00000, 0.20000

## FCN and flambda loss

In [12]:
runexp('mnist', 'flamb', PRIOR, 'fcn', SIGMAPRIOR, PMIN, LEARNING_RATE, MOMENTUM, LEARNING_RATE_PRIOR, MOMENTUM_PRIOR, delta=DELTA, delta_test=DELTA_TEST, mc_samples=MC_SAMPLES, train_epochs=TRAIN_EPOCHS, device=DEVICE, prior_epochs=70, perc_train=1.0, perc_prior=0.5, verbose=True, dropout_prob=0.2)

  1%|█▏                                                                                  | 1/70 [00:04<04:56,  4.30s/it]

-Epoch 0.00000, Train loss: 0.92539, Train err:  0.26757



  3%|██▍                                                                                 | 2/70 [00:08<04:53,  4.31s/it]

-Epoch 1.00000, Train loss: 0.25151, Train err:  0.07393



  4%|███▌                                                                                | 3/70 [00:12<04:45,  4.27s/it]

...


 54%|███████████████████████████████████████████▌                                     | 129/240 [00:09<00:07, 14.08it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 50/50 [14:12<00:00, 17.04s/it]

-Batch average epoch 49 results, Train obj: 0.01130, KL/n: 0.00039, NLL loss: 0.00510, Train 0-1 Error:  0.01247
-After optimising lambda: Train obj: 0.01104, KL/n: 0.00039, NLL loss: 0.00498, Train 0-1 Error:  0.01192, last lambda value: 0.99752



100%|███████████████████████████████████████████████████████████████████████████████████| 40/40 [00:36<00:00,  1.11it/s]

***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
flamb, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.04816, 0.02909, 0.04839, 0.00039, 0.02358, 0.04129, 0.00933, 0.02170, 0.01273, 0.01730, 0.00012, 0.01800, 0.01930, 1.00000, 0.50000


***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
flamb, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.04816, 0.02909, 0.04839, 0.00039, 0.02358, 0.04129, 0.00933, 0.02170, 0.01273, 0.01730, 0.00012, 0.01800, 0.01930, 1.00000, 0.50000

## FCN and fquad loss

In [10]:
runexp('mnist', 'fquad', PRIOR, 'fcn', SIGMAPRIOR, PMIN, LEARNING_RATE, MOMENTUM, LEARNING_RATE_PRIOR, MOMENTUM_PRIOR, delta=DELTA, delta_test=DELTA_TEST, mc_samples=MC_SAMPLES, train_epochs=TRAIN_EPOCHS, device=DEVICE, perc_train=1.0, verbose=True, dropout_prob=0.2)


  5%|████▏                                                                               | 1/20 [00:01<00:30,  1.60s/it]

-Epoch 0.00000, Train loss: 1.48034, Train err:  0.44308



 10%|████████▍                                                                           | 2/20 [00:03<00:29,  1.64s/it]

-Epoch 1.00000, Train loss: 0.66969, Train err:  0.15583



 15%|████████████▌                                                                       | 3/20 [00:04<00:28,  1.65s/it]

...


 54%|███████████████████████████████████████████▌                                     | 129/240 [00:06<00:06, 18.43it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 50/50 [10:28<00:00, 12.56s/it]

-Batch average epoch 49 results, Train obj: 0.01666, KL/n: 0.00017, NLL loss: 0.01338, Train 0-1 Error:  0.03264



100%|███████████████████████████████████████████████████████████████████████████████████| 40/40 [00:34<00:00,  1.15it/s]

***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
fquad, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.03767, 0.03758, 0.06985, 0.00017, 0.03267, 0.06324, 0.01553, 0.03740, 0.01525, 0.02930, 0.00039, 0.03010, 0.03320, 1.00000, 0.20000


***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
fquad, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.03767, 0.03758, 0.06985, 0.00017, 0.03267, 0.06324, 0.01553, 0.03740, 0.01525, 0.02930, 0.00039, 0.03010, 0.03320, 1.00000, 0.20000

## FCN and fbbb loss

In [11]:
runexp('mnist', 'bbb', PRIOR, 'fcn', SIGMAPRIOR, PMIN, LEARNING_RATE, MOMENTUM, LEARNING_RATE_PRIOR, MOMENTUM_PRIOR, delta=DELTA, delta_test=DELTA_TEST, mc_samples=MC_SAMPLES, train_epochs=TRAIN_EPOCHS, device=DEVICE, perc_train=1.0, verbose=True, dropout_prob=0.2)


  5%|████▏                                                                               | 1/20 [00:01<00:32,  1.70s/it]

-Epoch 0.00000, Train loss: 1.48034, Train err:  0.44308



 10%|████████▍                                                                           | 2/20 [00:03<00:30,  1.69s/it]

-Epoch 1.00000, Train loss: 0.66969, Train err:  0.15583



 15%|████████████▌                                                                       | 3/20 [00:05<00:28,  1.67s/it]

...


 69%|████████████████████████████████████████████████████████                         | 166/240 [00:08<00:03, 19.57it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 50/50 [10:28<00:00, 12.58s/it]

-Batch average epoch 49 results, Train obj: 0.10357, KL/n: 0.02194, NLL loss: 0.08163, Train 0-1 Error:  0.02343



100%|███████████████████████████████████████████████████████████████████████████████████| 40/40 [00:34<00:00,  1.15it/s]

***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
bbb, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.04294, 0.06616, 0.10689, 0.02184, 0.02109, 0.04840, 0.00976, 0.03240, 0.00785, 0.02320, 0.00023, 0.02370, 0.03320, 1.00000, 0.20000


***Final results***
Objective, Dataset, Sigma, pmin, LR, momentum, LR_prior, momentum_prior, kl_penalty, dropout, Obj_train, Risk_CE, Risk_01, KL, Train NLL loss, Train 01 error, Stch loss, Stch 01 error, Post mean loss, Post mean 01 error, Ens loss, Ens 01 error, 01 error prior net, perc_train, perc_prior
bbb, mnist, 0.03000, 0.00001, 0.00100, 0.95000, 0.00500, 0.99000,  1.00000, 0.20000, 0.04294, 0.06616, 0.10689, 0.02184, 0.02109, 0.04840, 0.00976, 0.03240, 0.00785, 0.02320, 0.00023, 0.02370, 0.03320, 1.00000, 0.20000